In [86]:
# importing libraries
import numpy as np
import pandas as pd
from pathlib import Path
import hvplot.pandas
import warnings
warnings.filterwarnings("ignore", category=FutureWarning)
import time
from sklearn.metrics import r2_score
from sklearn.preprocessing import StandardScaler
from tensorflow.keras.layers import Dense
from tensorflow.keras.models import Sequential
from tensorflow.keras.metrics import MeanSquaredError
from pandas.tseries.offsets import DateOffset
from sklearn.cluster import KMeans
from sklearn.decomposition import PCA
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
from bokeh.models.formatters import NumeralTickFormatter

In [87]:
all_values = pd.read_csv(Path("Resources/all_values_superset.csv"))
all_values['date'] = pd.to_datetime(all_values['date'], format='%Y-%m')
all_values.set_index('date', inplace=True)
all_values.drop(columns=['All-items 8', 'All-items excluding food', 'All-items excluding food and energy'], inplace=True)
all_values.dtypes

Composite_Benchmark_SA_BANCROFT_AND_AREA                           float64
Single_Family_Benchmark_SA_BANCROFT_AND_AREA                       float64
One_Storey_Benchmark_SA_BANCROFT_AND_AREA                          float64
Two_Storey_Benchmark_SA_BANCROFT_AND_AREA                          float64
Composite_Benchmark_SA_BARRIE_AND_AREA                             float64
                                                                    ...   
Clothing and footwear                                              float64
Transportation                                                     float64
Health and personal care                                           float64
Recreation, education and reading                                  float64
Alcoholic beverages, tobacco products and recreational cannabis    float64
Length: 174, dtype: object

In [88]:
scaler_all = StandardScaler()
all_scaler = scaler_all.fit(all_values)
all_values_scaled = all_scaler.transform(all_values)

all_values_scaled_df = pd.DataFrame(all_values_scaled, columns=all_values.columns, index=all_values.index)
all_values_scaled_df.head()

Composite_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                   
2008-06-01                                 -0.825918   
2008-07-01                                 -0.831709   
2008-08-01                                 -0.846185   
2008-09-01                                 -0.865487   
2008-10-01                                 -0.872242   

            Single_Family_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                       
2008-06-01                                     -0.825918   
2008-07-01                                     -0.831709   
2008-08-01                                     -0.846185   
2008-09-01                                     -0.865487   
2008-10-01                                     -0.872242   

            One_Storey_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                    
2008-06-01                                  -0.947581   
2008-07-01                                  -0.973779   
2008-08-01                                  -0.985006   
2008-09-01                                  -1.015882   
2008-10-01                                  -1.023367   

            Two_Storey_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                    
2008-06-01                                  -0.407433   
2008-07-01                                  -0.374424   
2008-08-01                                  -0.384427   
2008-09-01                                  -0.346415   
2008-10-01                                  -0.328410   

            Composite_Benchmark_SA_BARRIE_AND_AREA  \
date                                                 
2008-06-01                               -0.936442   
2008-07-01                               -0.943571   
2008-08-01                               -0.950192   
2008-09-01                               -0.948155   
2008-10-01                               -0.951720   

            Single_Family_Benchmark_SA_BARRIE_AND_AREA  \
date                                                     
2008-06-01                                   -0.935664   
2008-07-01                                   -0.943884   
2008-08-01                                   -0.951622   
2008-09-01                                   -0.949687   
2008-10-01                                   -0.952105   

            One_Storey_Benchmark_SA_BARRIE_AND_AREA  \
date                                                  
2008-06-01                                -0.932140   
2008-07-01                                -0.953696   
2008-08-01                                -0.970121   
2008-09-01                                -0.964988   
2008-10-01                                -0.956263   

            Two_Storey_Benchmark_SA_BARRIE_AND_AREA  \
date                                                  
2008-06-01                                -0.938398   
2008-07-01                                -0.937469   
2008-08-01                                -0.938862   
2008-09-01                                -0.940254   
2008-10-01                                -0.948142   

            Townhouse_Benchmark_SA_BARRIE_AND_AREA  \
date                                                 
2008-06-01                               -0.823496   
2008-07-01                               -0.817839   
2008-08-01                               -0.812889   
2008-09-01                               -0.811475   
2008-10-01                               -0.815011   

            Apartment_Benchmark_SA_BARRIE_AND_AREA  ...       ITB  Bank Rate  \
date                                                ...                        
2008-06-01                               -0.888138  ... -0.804832   2.568481   
2008-07-01                               -0.880624  ... -0.865314   2.568481   
2008-08-01                               -0.869769  ... -0.862638   2.568481   
2008-09-01                               -0.863925  ... -0.69

In [89]:
targets = [col for col in all_values_scaled_df.columns.tolist() if col.find('Benchmark') > 0]

In [90]:
y = all_values_scaled_df[targets]

In [91]:
X = all_values_scaled_df.drop(columns = targets)

In [92]:
y.shape

(176, 161)

In [93]:
y.head()

Composite_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                   
2008-06-01                                 -0.825918   
2008-07-01                                 -0.831709   
2008-08-01                                 -0.846185   
2008-09-01                                 -0.865487   
2008-10-01                                 -0.872242   

            Single_Family_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                       
2008-06-01                                     -0.825918   
2008-07-01                                     -0.831709   
2008-08-01                                     -0.846185   
2008-09-01                                     -0.865487   
2008-10-01                                     -0.872242   

            One_Storey_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                    
2008-06-01                                  -0.947581   
2008-07-01                                  -0.973779   
2008-08-01                                  -0.985006   
2008-09-01                                  -1.015882   
2008-10-01                                  -1.023367   

            Two_Storey_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                    
2008-06-01                                  -0.407433   
2008-07-01                                  -0.374424   
2008-08-01                                  -0.384427   
2008-09-01                                  -0.346415   
2008-10-01                                  -0.328410   

            Composite_Benchmark_SA_BARRIE_AND_AREA  \
date                                                 
2008-06-01                               -0.936442   
2008-07-01                               -0.943571   
2008-08-01                               -0.950192   
2008-09-01                               -0.948155   
2008-10-01                               -0.951720   

            Single_Family_Benchmark_SA_BARRIE_AND_AREA  \
date                                                     
2008-06-01                                   -0.935664   
2008-07-01                                   -0.943884   
2008-08-01                                   -0.951622   
2008-09-01                                   -0.949687   
2008-10-01                                   -0.952105   

            One_Storey_Benchmark_SA_BARRIE_AND_AREA  \
date                                                  
2008-06-01                                -0.932140   
2008-07-01                                -0.953696   
2008-08-01                                -0.970121   
2008-09-01                                -0.964988   
2008-10-01                                -0.956263   

            Two_Storey_Benchmark_SA_BARRIE_AND_AREA  \
date                                                  
2008-06-01                                -0.938398   
2008-07-01                                -0.937469   
2008-08-01                                -0.938862   
2008-09-01                                -0.940254   
2008-10-01                                -0.948142   

            Townhouse_Benchmark_SA_BARRIE_AND_AREA  \
date                                                 
2008-06-01                               -0.823496   
2008-07-01                               -0.817839   
2008-08-01                               -0.812889   
2008-09-01                               -0.811475   
2008-10-01                               -0.815011   

            Apartment_Benchmark_SA_BARRIE_AND_AREA  ...  \
date                                                ...   
2008-06-01                               -0.888138  ...   
2008-07-01                               -0.880624  ...   
2008-08-01                               -0.869769  ...   
2008-09-01                               -0.863925  ...   
2008-10-01                               -0.898157  ...   

            Single_Family_Benchmark_SA_WINDSOR_

In [94]:
X.head()

Lumber      Wood       XHB       ITB  Bank Rate      Food  \
date                                                                      
2008-06-01 -0.664592 -0.505146 -0.929491 -0.804832   2.568481 -1.744835   
2008-07-01 -0.637850 -0.524583 -1.017591 -0.865314   2.568481 -1.689366   
2008-08-01 -0.605399 -0.486888 -0.959232 -0.862638   2.568481 -1.633897   
2008-09-01 -0.720345 -0.442713 -0.811089 -0.690289   2.568481 -1.550693   
2008-10-01 -0.881425 -0.780796 -0.937908 -0.775928   1.604616 -1.516025   

             Shelter  Household operations, furnishings and equipment  \
date                                                                    
2008-06-01 -1.183779                                        -1.929083   
2008-07-01 -1.099725                                        -1.901250   
2008-08-01 -1.057698                                        -1.901250   
2008-09-01 -1.116536                                        -1.776002   
2008-10-01 -1.108130                                        -1.803835   

            Clothing and footwear  Transportation  Health and personal care  \
date                                                                          
2008-06-01               0.208160       -0.678934                 -1.897463   
2008-07-01               0.726901       -0.678934                 -1.884047   
2008-08-01               0.402688       -0.795051                 -1.763302   
2008-09-01               0.208160       -0.802309                 -1.776718   
2008-10-01              -0.634795       -1.092603                 -1.763302   

            Recreation, education and reading  \
date                                            
2008-06-01                          -1.378353   
2008-07-01                          -1.394462   
2008-08-01                          -1.346137   
2008-09-01                          -1.362245   
2008-10-01                          -1.394462   

            Alcoholic beverages, tobacco products and recreational cannabis  
date                                                                         
2008-06-01                                          -1.491493                
2008-07-01                                          -1.497273                
2008-08-01                                          -1.503054                
2008-09-01                                          -1.474150                
2008-10-01                                          -1.474150

In [95]:
all_values_scaled_df.hvplot(
    height=800,
    width=1600
)

:NdOverlay   [Variable]
   :Curve   [date]   (value)

In [96]:
X_train, X_test, y_train, y_test = train_test_split(X, y)
X_train
X_test.sort_index(ascending=True, inplace=True)
y_train
y_test.sort_index(ascending=True, inplace=True)
y_test_size = y_test.shape[0]
y_test_size

44

In [97]:
# scaler = StandardScaler()

# X_scaler = scaler.fit(X_train)
# X_train_scaled = X_scaler.transform(X_train)
# X_test_scaled = X_scaler.transform(X_test)

In [98]:
# Neural network parameters
n_input_feats = len(X.columns)

n_outputs = 161

hidden_nodes_layer1 = 128
hidden_nodes_layer2 = 256
hidden_nodes_layer3 = 256
# hidden_nodes_layer4 = 4
print(f"""
Neural Network Parameters:
--------------------------
Input Features: {n_input_feats}
Layers:         3
Layer1 Nodes:   {hidden_nodes_layer1}
Layer2 Nodes:   {hidden_nodes_layer2}
Layer3 Nodes:   {hidden_nodes_layer3}
Output Nodes:   {n_outputs}
""")


Neural Network Parameters:
--------------------------
Input Features: 13
Layers:         3
Layer1 Nodes:   128
Layer2 Nodes:   256
Layer3 Nodes:   256
Output Nodes:   161



In [99]:
# define model
nn = Sequential()

In [100]:
# Add the first hidden layer
nn.add(Dense(
    units=hidden_nodes_layer1,
    input_dim = n_input_feats,
    activation='relu',
    name='hidden1'
))

In [101]:
# Add the second hidden layer
nn.add(Dense(
    units=hidden_nodes_layer2,
    activation='relu',
    name='hidden2'
))

In [102]:
# Add the third hidden layer
nn.add(Dense(
    units=hidden_nodes_layer3,
    activation='relu',
    name='hidden3'
))

In [103]:
# Add output
nn.add(Dense(
    n_outputs,
    activation='linear',
    name='output'
))

In [104]:
# Display the Sequential model summary
nn.summary()

Model: "sequential_2"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 hidden1 (Dense)             (None, 128)               1792      
                                                                 
 hidden2 (Dense)             (None, 256)               33024     
                                                                 
 hidden3 (Dense)             (None, 256)               65792     
                                                                 
 output (Dense)              (None, 161)               41377     
                                                                 
Total params: 141,985
Trainable params: 141,985
Non-trainable params: 0
_________________________________________________________________


In [105]:
# Compile the Sequential model
nn.compile(loss='mean_squared_error', optimizer='adam', metrics=[MeanSquaredError()])

In [106]:
# Fit the model using 50 epochs and the training data
model = nn.fit(
    X_train,
    y_train,
    batch_size=10,
    validation_split=0.2,
    epochs=100
)

Epoch 1/100
11/11 [==============================] - 4s 88ms/step - loss: 0.8181 - mean_squared_error: 0.8181 - val_loss: 0.2649 - val_mean_squared_error: 0.2649
Epoch 2/100
11/11 [==============================] - 0s 19ms/step - loss: 0.2450 - mean_squared_error: 0.2450 - val_loss: 0.0858 - val_mean_squared_error: 0.0858
Epoch 3/100
11/11 [==============================] - 0s 25ms/step - loss: 0.0861 - mean_squared_error: 0.0861 - val_loss: 0.0495 - val_mean_squared_error: 0.0495
Epoch 4/100
11/11 [==============================] - 0s 24ms/step - loss: 0.0552 - mean_squared_error: 0.0552 - val_loss: 0.0364 - val_mean_squared_error: 0.0364
Epoch 5/100
11/11 [==============================] - 0s 20ms/step - loss: 0.0373 - mean_squared_error: 0.0373 - val_loss: 0.0316 - val_mean_squared_error: 0.0316
Epoch 6/100
11/11 [==============================] - 0s 14ms/step - loss: 0.0288 - mean_squared_error: 0.0288 - val_loss: 0.0309 - val_mean_squared_error: 0.0309
Epoch 7/100
11/11 [=========

In [107]:
# R2 score for training
train_pred = nn.predict(X_train)
training_r2 = r2_score(y_train.values, train_pred)
# model_loss, model_accuracy = nn.evaluate(X_test, y_test)
training_r2

5/5 [==============================] - 0s 3ms/step


0.9576546656392053

In [108]:
# Create a DataFrame with the history dictionary
model_df = pd.DataFrame(model.history, index=range(1, len(model.history["loss"]) + 1))

In [109]:
# Plot the loss
model_df.hvplot(
    y="val_loss",
    
)

:Curve   [index]   (val_loss)

In [110]:
# Plot the accuracy
model_df.hvplot(y="mean_squared_error")

:Curve   [index]   (mean_squared_error)

In [123]:
model_df[['val_loss', 'mean_squared_error']].hvplot(
    height=800,
    width=2000
)

:NdOverlay   [Variable]
   :Curve   [index]   (value)

In [112]:
predictions = nn.predict(X_test)
# predictions = nn.predict(X_test.sort_index(ascending=True))

2/2 [==============================] - 0s 4ms/step


In [113]:
# R2 score from test
test_r2 = r2_score(y_test.values, predictions)
# test_r2 = r2_score(y_test.sort_index(ascending=True).values, predictions)
test_r2

0.9647578907740243

In [114]:
all_values_pred = nn.predict(X)
all_values_pred.shape

6/6 [==============================] - 0s 3ms/step


(176, 161)

In [115]:
all_feats_pred = nn.predict(X)
all_feats_pred_df = pd.DataFrame(all_feats_pred, columns=y.columns, index=X.index)
all_preds_feats_scaled_df = pd.concat([all_feats_pred_df, X], axis=1)
all_preds_feats_descaled = all_scaler.inverse_transform(all_preds_feats_scaled_df)
all_preds_feats_descaled_df = pd.DataFrame(all_preds_feats_descaled, columns=all_preds_feats_scaled_df.columns, index=all_preds_feats_scaled_df.index)
all_preds_descaled_df = all_preds_feats_descaled_df[targets]
all_preds_descaled_df.columns = ['PRED_'+col for col in all_preds_descaled_df.columns]
all_preds_descaled_df
# all_preds_feats_descaled_df
# all_pred_real = all_values_scaled_df.copy()
# all_pred_real['Composite'] = all_values_pred
# all_values_descaled = all_scaler.inverse_transform(all_pred_real)
# all_values_descaled_df = pd.DataFrame(all_values_descaled, columns=all_values_scaled_df.columns, index=all_values_scaled_df.index)
# all_values_descaled_df
# all_values_descaled_df['Predicted'] = all_values_descaled_df['Composite']
# all_values_descaled_df['Composite'] = all_values['Composite']
# all_values_descaled_df

6/6 [==============================] - 0s 7ms/step


PRED_Composite_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                        
2008-06-01                                  156462.890899   
2008-07-01                                  157383.435553   
2008-08-01                                  159516.970366   
2008-09-01                                  157092.311739   
2008-10-01                                  151163.661762   
...                                                   ...   
2022-09-01                                  505077.639641   
2022-10-01                                  493998.864439   
2022-11-01                                  499679.833437   
2022-12-01                                  486950.106986   
2023-01-01                                  509990.941507   

            PRED_Single_Family_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                            
2008-06-01                                      157634.149008   
2008-07-01                                      157719.058319   
2008-08-01                                      160751.620180   
2008-09-01                                      157608.468697   
2008-10-01                                      153236.812640   
...                                                       ...   
2022-09-01                                      507662.741538   
2022-10-01                                      499631.709102   
2022-11-01                                      506564.182549   
2022-12-01                                      495827.292699   
2023-01-01                                      518719.085069   

            PRED_One_Storey_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                         
2008-06-01                                   150048.718658   
2008-07-01                                   153166.202882   
2008-08-01                                   154126.892059   
2008-09-01                                   151178.698390   
2008-10-01                                   144748.307460   
...                                                    ...   
2022-09-01                                   515668.129723   
2022-10-01                                   505611.172505   
2022-11-01                                   513320.053041   
2022-12-01                                   502615.212576   
2023-01-01                                   520805.302374   

            PRED_Two_Storey_Benchmark_SA_BANCROFT_AND_AREA  \
date                                                         
2008-06-01                                   185562.667397   
2008-07-01                                   188058.460713   
2008-08-01                                   188490.320091   
2008-09-01                                   186239.152048   
2008-10-01                                   183941.914357   
...                                                    ...   
2022-09-01                                   476248.724717   
2022-10-01                                   460768.178898   
2022-11-01                                   462235.924576   
2022-12-01                                   449155.683991   
2023-01-01                                   468224.126731   

            PRED_Composite_Benchmark_SA_BARRIE_AND_AREA  \
date                                                      
2008-06-01                                244843.569916   
2008-07-01                                249579.727532   
2008-08-01                                250495.361886   
2008-09-01                                250897.957756   
2008-10-01                                242211.159186   
...                                                 ...   
2022-09-01                                854766.516030   
2022-10-01                                827853.677963   
2022-11-01                                841993.001279   
2022-12-01                                818422.866495   
2023-01-01                                847799.9

In [116]:
bancroft_pred_compare_df = pd.concat([all_preds_descaled_df.loc[:,'PRED_Composite_Benchmark_SA_BANCROFT_AND_AREA'], all_values.loc[:,'Composite_Benchmark_SA_BANCROFT_AND_AREA']], axis=1)
bancroft_pred_compare_df.hvplot(
    height=800,
    width=1600
)

:NdOverlay   [Variable]
   :Curve   [date]   (value)

In [117]:
oakville_pred_compare_df = pd.concat([all_preds_descaled_df.loc[:,'PRED_Two_Storey_Benchmark_SA_OAKVILLE_MILTON'], all_values.loc[:,'Two_Storey_Benchmark_SA_OAKVILLE_MILTON']], axis=1)
oakville_pred_compare_df.hvplot(
    height=800,
    width=1600
)

:NdOverlay   [Variable]
   :Curve   [date]   (value)

In [125]:
all_targets_pred_compare_df = pd.concat([all_preds_descaled_df, all_values[targets]], axis=1)
all_targets_pred_compare_df.hvplot(
    xlabel='Date', 
    ylabel='Price', 
    title='Actual and Predicted Index',
    height=800,
    width=1600,
    legend=False    
).opts(
    yformatter=NumeralTickFormatter(format="0,0")
)

:NdOverlay   [Variable]
   :Curve   [date]   (value)

In [120]:
nn_json = nn.to_json()

file_path = ("Models/model3.json")
with open(file_path, "w") as json_file:
    json_file.write(nn_json)

In [121]:
file_path = "Models/model3.h5"
nn.save_weights(file_path)

In [79]:
def mean_absolute_percentage_error(y_true, y_pred): 
    y_true, y_pred = np.array(y_true), np.array(y_pred)
    return np.mean(np.abs((y_true - y_pred) / y_true)) * 100

def weighted_absolute_percentage_error(y_true, y_pred):
    return 100 / len(y_true) * np.sum(np.abs((y_true - y_pred) / y_true))

def weighted_mean_absolute_percentage_error(y_true, y_pred):
    return 100 / sum(y_true) * np.sum(np.abs(y_true - y_pred))

In [82]:
# Generate predictions
y_pred = nn.predict(X_test)

# Calculate R-Squared
r2 = r2_score(y_test, y_pred)

# Calculate Mean Absolute Error
mae = mean_absolute_error(y_test, y_pred)

# Calculate Mean Absolute Percentage Error
mape = mean_absolute_percentage_error(y_test, y_pred)

# Calculate Mean Squared Error
mse = mean_squared_error(y_test, y_pred)

# Calculate Root Mean Squared Error
rmse = np.sqrt(mse)

2/2 [==============================] - 0s 5ms/step


In [84]:
print(f"R-Squared: {r2}")
print(f"Mean Absolute Error: {mae}")
print(f"Mean Absolute Percentage Error: {mape}")
print(f"Mean Squared Error: {mse}")
print(f"Root Mean Squared Error: {rmse}")


R-Squared: 0.988579310366157
Mean Absolute Error: 0.06405685077016317
Mean Absolute Percentage Error: 24.720600483659982
Mean Squared Error: 0.010621614314503598
Root Mean Squared Error: 0.1030612163449646
